# Capstone Project - The Battle of Neighborhoods

### Import Libraries.

In [1]:
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import numpy as np

from bs4 import BeautifulSoup # library to parse HTML and XML documents
import requests # library to handle requests

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1d             |       h516909a_0         2.1 MB  conda-forge
    certifi-2019.11.28         |           py36_0         149 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ca-certificates-2019.11.28 |       hecc5488_0         145 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

### Load and explore the data.

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

Notice how all the relevant data is in the features key, which is basically a list of the neighborhoods. So, let's define a new variable that includes this data.

In [8]:
neighborhoods_data = newyork_data['features']

### Tranform the data into a *pandas* dataframe

The next task is essentially transforming this data of nested Python dictionaries into a *pandas* dataframe. So let's start by creating an empty dataframe.

In [9]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Then let's loop through the data and fill the dataframe one row at a time.

In [10]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

Quickly examine the resulting dataframe.

In [11]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [12]:
 neighborhoods.shape

(306, 4)

### Use geopy library to get the latitude and longitude values of New York City.

In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


### Create a map of New York with neighborhoods superimposed on top.

In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

Let's simplify the above map and segment and cluster only the neighborhoods in Manhattan. So let's slice the original dataframe and create a new dataframe of the Manhattan data.

### Use Define Foursquare Credentials and Version

In [15]:
CLIENT_ID = '3QYYHW0VOX0UOC0OU5UBUDEYK3RR01QV3WMHTG0USOO2T4XR' # your Foursquare ID
CLIENT_SECRET = '1WBETSYFZMX3ZFNHJRAOFBJSBUWUC1HC4KFWGIZP1KEQSCLB' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 3QYYHW0VOX0UOC0OU5UBUDEYK3RR01QV3WMHTG0USOO2T4XR
CLIENT_SECRET:1WBETSYFZMX3ZFNHJRAOFBJSBUWUC1HC4KFWGIZP1KEQSCLB


### Let's define a query to search for Korean Restaurant that is within 5000 metres from New York city.

In [41]:
search_query = 'Korean Restaurant'
radius = 5000
print(search_query + ' .... OK!')

Korean Restaurant .... OK!


Define the corresponding URL.

In [42]:
url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, search_query, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/search?client_id=3QYYHW0VOX0UOC0OU5UBUDEYK3RR01QV3WMHTG0USOO2T4XR&client_secret=1WBETSYFZMX3ZFNHJRAOFBJSBUWUC1HC4KFWGIZP1KEQSCLB&ll=40.7127281,-74.0060152&v=20180605&query=Korean Restaurant&radius=5000&limit=100'

Send the GET Request and examine the results.

In [43]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5dec6401c9497946caa1e9bc'},
 'response': {'venues': [{'id': '4e4c4ee8bd413c4cc66863d4',
    'name': 'She Ja Meh Korean Restaurant',
    'location': {'address': '26 John St',
     'lat': 40.709644,
     'lng': -74.008579,
     'labeledLatLngs': [{'label': 'display',
       'lat': 40.709644,
       'lng': -74.008579}],
     'distance': 405,
     'postalCode': '10038',
     'cc': 'US',
     'city': 'New York',
     'state': 'NY',
     'country': 'United States',
     'formattedAddress': ['26 John St',
      'New York, NY 10038',
      'United States']},
    'categories': [{'id': '4bf58dd8d48988d113941735',
      'name': 'Korean Restaurant',
      'pluralName': 'Korean Restaurants',
      'shortName': 'Korean',
      'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/korean_',
       'suffix': '.png'},
      'primary': True}],
    'referralId': 'v-1575773190',
    'hasPerk': False},
   {'id': '4f325eec19836c91c7d12c86',
    'name': 'Korean 

Get relevant part of JSON and transform it into a pandas dataframe

In [46]:
# assign relevant part of JSON to venues
venues = results['response']['venues']

# tranform venues into a dataframe
df = json_normalize(venues)
df.head()

categories delivery.id  \
0  [{'id': '4bf58dd8d48988d113941735', 'name': 'K...         NaN   
1  [{'id': '4d4b7105d754a06374d81259', 'name': 'F...         NaN   
2  [{'id': '4bf58dd8d48988d1c1941735', 'name': 'M...         NaN   
3  [{'id': '4bf58dd8d48988d113941735', 'name': 'K...         NaN   
4  [{'id': '4bf58dd8d48988d1f5931735', 'name': 'D...      296411   

                delivery.provider.icon.name  \
0                                       NaN   
1                                       NaN   
2                                       NaN   
3                                       NaN   
4  /delivery_provider_seamless_20180129.png   

              delivery.provider.icon.prefix delivery.provider.icon.sizes  \
0                                       NaN                          NaN   
1                                       NaN                          NaN   
2                                       NaN                          NaN   
3                                       NaN                          NaN   
4  https://fastly.4sqi.net/img/general/cap/                     [40, 50]   

  delivery.provider.name                                       delivery.url  \
0                    NaN                                                NaN   
1                    NaN                                                NaN   
2                    NaN                                                NaN   
3                    NaN                                                NaN   
4               seamless  https://www.seamless.com/menu/jing-fong-restau...   

   hasPerk                        id location.address location.cc  \
0    False  4e4c4ee8bd413c4cc66863d4       26 John St          US   
1    False  4f325eec19836c91c7d12c86      22 W 8th St          US   
2    False  4c22530f7e85c928f7d7bb21     51 W 29th St          US   
3    False  4bb930f11261d13ade6ee998   774 W Side Ave          US   
4    False  3fd66200f964a520d5e31ee3  20 Elizabeth St          US   

  location.city location.country    location.crossStreet  location.distance  \
0      New York    United States                     NaN                405   
1      New York    United States                     NaN               2339   
2      New York    United States                     NaN               4017   
3   Jersey City    United States           Duncan Avenue               6127   
4      New York    United States  btwn Bayard & Canal St                821   

                           location.formattedAddress  \
0    [26 John St, New York, NY 10038, United States]   
1   [22 W 8th St, New York, NY 10011, United States]   
2  [51 W 29th St, New York, NY 10001, United States]   
3  [774 W Side Ave (Duncan Avenue), Jersey City, ...   
4  [20 Elizabeth St (btwn Bayard & Canal St), New...   

                             location.labeledLatLngs  location.lat  \
0  [{'label': 'display', 'lat': 40.709644, 'lng':...     40.709644   
1  [{'label': 'display', 'lat': 40.732749, 'lng':...     40.732749   
2  [{'label': 'display', 'lat': 40.74662100000000...     40.746621   
3  [{'label': 'display', 'lat': 40.726788, 'lng':...     40.726788   
4  [{'label': 'display', 'lat': 40.7158812029412,...     40.715881   

   location.lng location.neighborhood location.postalCode location.state  \
0    -74.008579                   NaN               10038             NY   
1    -73.997570                   NaN               10011             NY   
2    -73.989661                   NaN               10001             NY   
3    -74.076239                   NaN               07306             NJ   
4    -73.997209                   NaN               10013             NY   

                           name    referralId venuePage.id  
0  She Ja Meh Korean Restaurant  v-1575773190          NaN  
1             Korean Restaurant  v-1575773190          NaN  
2     Mexican/Korean Restaurant  v-1575773190          NaN  
3   Hwa Kwang Korean restaurant  v-1575773190          NaN  
4    Jin

### Define information of interest and filter dataframe.

In [47]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in dataframe.columns if col.startswith('location.')] + ['id']
df_filtered = df.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
df_filtered['categories'] = df_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
df_filtered.columns = [column.split('.')[-1] for column in df_filtered.columns]

df_filtered.head()

name          categories          address  cc  \
0  She Ja Meh Korean Restaurant   Korean Restaurant       26 John St  US   
1             Korean Restaurant                Food      22 W 8th St  US   
2     Mexican/Korean Restaurant  Mexican Restaurant     51 W 29th St  US   
3   Hwa Kwang Korean restaurant   Korean Restaurant   774 W Side Ave  US   
4    Jing Fong Restaurant 金豐大酒樓  Dim Sum Restaurant  20 Elizabeth St  US   

          city        country             crossStreet  distance  \
0     New York  United States                     NaN       405   
1     New York  United States                     NaN      2339   
2     New York  United States                     NaN      4017   
3  Jersey City  United States           Duncan Avenue      6127   
4     New York  United States  btwn Bayard & Canal St       821   

                                    formattedAddress  \
0    [26 John St, New York, NY 10038, United States]   
1   [22 W 8th St, New York, NY 10011, United States]   
2  [51 W 29th St, New York, NY 10001, United States]   
3  [774 W Side Ave (Duncan Avenue), Jersey City, ...   
4  [20 Elizabeth St (btwn Bayard & Canal St), New...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 40.709644, 'lng':...  40.709644 -74.008579   
1  [{'label': 'display', 'lat': 40.732749, 'lng':...  40.732749 -73.997570   
2  [{'label': 'display', 'lat': 40.74662100000000...  40.746621 -73.989661   
3  [{'label': 'display', 'lat': 40.726788, 'lng':...  40.726788 -74.076239   
4  [{'label': 'display', 'lat': 40.7158812029412,...  40.715881 -73.997209   

  neighborhood postalCode state                        id  
0          NaN      10038    NY  4e4c4ee8bd413c4cc66863d4  
1          NaN      10011    NY  4f325eec19836c91c7d12c86  
2          NaN      10001    NY  4c22530f7e85c928f7d7bb21  
3          NaN      07306    NJ  4bb930f11261d13ade6ee998  
4          NaN      10013    NY  3fd66200f964a520d5e31ee3

### Create a dataframe for Korean Restaurants within 5000 meters from New York city.

In [60]:
krest = df_filtered[["name","categories"]]
krest = krest[krest.categories.str.contains('Korean Restaurant')]
krest

name         categories
0   She Ja Meh Korean Restaurant  Korean Restaurant
3    Hwa Kwang Korean restaurant  Korean Restaurant
19                    The Kunjip  Korean Restaurant
28                    Bangia 반지하  Korean Restaurant
38                     New Wonjo  Korean Restaurant

### Now we create a function to get the top 100 venues that are in all neighborhoods within a radius of 5000 meters in New York city.

In [24]:
LIMIT = 100
Radius = 5000

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
       # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Now write the code to run the above function on each neighborhood and create a new dataframe called ny_venues.

In [66]:
ny_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude'])

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [67]:
ny_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3             Shell       40.894187       -73.845862     Gas Station  
4           Dunkin'       40.890459       -73.849089      Donut Shop

In [68]:
# check if the results contain "Korean Restaurant"
"Korean Restaurant" in ny_venues['Venue Category'].unique()

True

### Let's Analyze Each Neighborhood.

In [69]:
# one hot encoding
ny_onehot = pd.get_dummies(ny_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
ny_onehot['Neighborhood'] = ny_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [ny_onehot.columns[-1]] + list(ny_onehot.columns[:-1])
ny_onehot = ny_onehot[fixed_columns]

ny_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  Airport Terminal  American Restaurant  Antique Shop  \
0                   0                 0                    0             0   
1                   0                 0                    0             0   
2                   0                 0                    0             0   
3                   0                 0                    0             0   
4                   0                 0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0          0                0         0            0           0   
1      0          0                0         0            0           0   
2      0          0                0         0            0           0   
3      0          0                0         0            0           0   
4      0          0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category.

In [70]:
ny_grouped = ny_onehot.groupby('Neighborhood').mean().reset_index()
ny_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.020408   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.013889           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.076923           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.022222           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030303           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.000000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.030612           0.000000   
59                  Co-op City     0.000000           0.00

### Lest's check how many Korean Restaurants in all Neighborhoods.

In [72]:
len(ny_grouped[ny_grouped["Korean Restaurant"] > 0])

26

### Let´s create a new DataFrame by taking the mean of the frequency (only Korean restaurants) of occurrence of each Neighborhood.

In [73]:
df_kr = ny_grouped[["Neighborhood","Korean Restaurant"]]

In [74]:
df_kr

Neighborhood  Korean Restaurant
0                     Allerton           0.000000
1                     Annadale           0.000000
2                Arden Heights           0.000000
3                    Arlington           0.000000
4                     Arrochar           0.000000
5                      Arverne           0.000000
6                      Astoria           0.010000
7              Astoria Heights           0.000000
8                   Auburndale           0.052632
9                   Bath Beach           0.000000
10           Battery Park City           0.000000
11                   Bay Ridge           0.000000
12                 Bay Terrace           0.000000
13                  Baychester           0.000000
14                     Bayside           0.013889
15                   Bayswater           0.000000
16                Bedford Park           0.000000
17          Bedford Stuyvesant           0.000000
18                  Beechhurst           0.000000
19                    Bellaire           0.000000
20                Belle Harbor           0.000000
21                   Bellerose           0.000000
22                     Belmont           0.000000
23                 Bensonhurst           0.000000
24                Bergen Beach           0.000000
25                  Blissville           0.000000
26                  Bloomfield           0.000000
27                 Boerum Hill           0.000000
28                Borough Park           0.000000
29                Breezy Point           0.000000
30                   Briarwood           0.000000
31              Brighton Beach           0.022222
32               Broad Channel           0.000000
33           Broadway Junction           0.000000
34                   Bronxdale           0.000000
35            Brooklyn Heights           0.000000
36                  Brookville           0.000000
37                 Brownsville           0.000000
38                  Bulls Head           0.000000
39                    Bushwick           0.012987
40                Butler Manor           0.000000
41             Cambria Heights           0.000000
42                    Canarsie           0.000000
43               Carnegie Hill           0.000000
44             Carroll Gardens           0.000000
45                 Castle Hill           0.000000
46           Castleton Corners           0.000000
47              Central Harlem           0.000000
48                  Charleston           0.000000
49                     Chelsea           0.000000
50                   Chinatown           0.010000
51                 City Island           0.000000
52                   City Line           0.000000
53                Civic Center           0.000000
54           Claremont Village           0.000000
55                Clason Point           0.000000
56                     Clifton           0.000000
57                     Clinton           0.010000
58                Clinton Hill           0.000000
59                  Co-op City           0.000000
60                 Cobble Hill           0.000000
61               College Point           0.000000
62                     Concord           0.000000
63                   Concourse           0.000000
64           Concourse Village           0.000000
65                Coney Island           0.000000
66                      Corona           0.000000
67                Country Club           0.000000
68               Crown Heights           0.000000
69               Cypress Hills           0.000000
70                 Ditmas Park           0.000000
71                Dongan Hills           0.000000
72                  Douglaston           0.000000
73                    Downtown           0.000000
74                       Dumbo           0.000000
75               Dyker Heights           0.000000
76               East Elmhurst           0.000000
77               East Flatbush           0.000000
78                 East Harlem           0.000000
79               E

### Now we cluster Neighborhoods setting for 3 clusters.

In [75]:
# set number of clusters
kclusters = 3

kr_clustering = df_kr.drop(["Neighborhood"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(kr_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 0, 0, 2, 0], dtype=int32)

In [76]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
kr_merged = df_kr.copy()

# add clustering labels
kr_merged["Cluster Labels"] = kmeans.labels_

In [77]:
# merge ny_grouped with toronto_data to add latitude/longitude for each neighborhood
kr_merged = kr_merged.join(neighborhoods.set_index("Neighborhood"), on="Neighborhood")

kr_merged.head()

Neighborhood  Korean Restaurant  Cluster Labels        Borough   Latitude  \
0       Allerton                0.0               0          Bronx  40.865788   
1       Annadale                0.0               0  Staten Island  40.538114   
2  Arden Heights                0.0               0  Staten Island  40.549286   
3      Arlington                0.0               0  Staten Island  40.635325   
4       Arrochar                0.0               0  Staten Island  40.596313   

   Longitude  
0 -73.859319  
1 -74.178549  
2 -74.185887  
3 -74.165104  
4 -74.067124

In [78]:
kr_merged.loc[kr_merged['Cluster Labels'] == 0]

Neighborhood  Korean Restaurant  Cluster Labels  \
0                     Allerton           0.000000               0   
1                     Annadale           0.000000               0   
2                Arden Heights           0.000000               0   
3                    Arlington           0.000000               0   
4                     Arrochar           0.000000               0   
5                      Arverne           0.000000               0   
6                      Astoria           0.010000               0   
7              Astoria Heights           0.000000               0   
9                   Bath Beach           0.000000               0   
10           Battery Park City           0.000000               0   
11                   Bay Ridge           0.000000               0   
12                 Bay Terrace           0.000000               0   
12                 Bay Terrace           0.000000               0   
13                  Baychester           0.000000               0   
14                     Bayside           0.013889               0   
15                   Bayswater           0.000000               0   
16                Bedford Park           0.000000               0   
17          Bedford Stuyvesant           0.000000               0   
18                  Beechhurst           0.000000               0   
19                    Bellaire           0.000000               0   
20                Belle Harbor           0.000000               0   
21                   Bellerose           0.000000               0   
22                     Belmont           0.000000               0   
23                 Bensonhurst           0.000000               0   
24                Bergen Beach           0.000000               0   
25                  Blissville           0.000000               0   
26                  Bloomfield           0.000000               0   
27                 Boerum Hill           0.000000               0   
28                Borough Park           0.000000               0   
29                Breezy Point           0.000000               0   
30                   Briarwood           0.000000               0   
32               Broad Channel           0.000000               0   
33           Broadway Junction           0.000000               0   
34                   Bronxdale           0.000000               0   
35            Brooklyn Heights           0.000000               0   
36                  Brookville           0.000000               0   
37                 Brownsville           0.000000               0   
38                  Bulls Head           0.000000               0   
39                    Bushwick           0.012987               0   
40                Butler Manor           0.000000               0   
41             Cambria Heights           0.000000               0   
42                    Canarsie           0.000000               0   
43               Carnegie Hill           0.000000               0   
44             Carroll Gardens           0.000000               0   
45                 Castle Hill           0.000000               0   
46           Castleton Corners           0.000000               0   
47              Central Harlem           0.000000               0   
48                  Charleston           0.000000               0   
49                     Chelsea           0.000000               0   
49                     Chelsea           0.000000               0   
50                   Chinatown           0.010000               0   
51                 City Island           0.000000               0   
52                   City Line           0.000000               0   
53                Civic Center           0.000000               0   
54           Claremont Village           0.000000               0   
55                Clason Point           0.000000               0   
56                     Clifton           0.000000               0   
57              

In [79]:
kr_merged.loc[kr_merged['Cluster Labels'] == 1]

Neighborhood  Korean Restaurant  Cluster Labels    Borough   Latitude  \
174    Midtown South           0.150000               1  Manhattan  40.748510   
185      Murray Hill           0.149660               1  Manhattan  40.748303   
185      Murray Hill           0.149660               1     Queens  40.764126   
197  Oakland Gardens           0.130435               1     Queens  40.745619   

     Longitude  
174 -73.988713  
185 -73.978332  
185 -73.812763  
197 -73.754950

In [80]:
kr_merged.loc[kr_merged['Cluster Labels'] == 2]

Neighborhood  Korean Restaurant  Cluster Labels        Borough  \
8           Auburndale           0.052632               2         Queens   
31      Brighton Beach           0.022222               2       Brooklyn   
81        East Village           0.020000               2      Manhattan   
100           Flushing           0.035088               2         Queens   
105      Fort Hamilton           0.015873               2       Brooklyn   
155        Little Neck           0.039216               2         Queens   
163   Manhattan Valley           0.020000               2      Manhattan   
188           New Dorp           0.038462               2  Staten Island   
206         Park Slope           0.028571               2       Brooklyn   
230          Ridgewood           0.025000               2         Queens   
253         South Side           0.020000               2       Brooklyn   
263  Sunnyside Gardens           0.030000               2         Queens   
291       Williamsburg           0.028571               2       Brooklyn   

      Latitude  Longitude  
8    40.761730 -73.791762  
31   40.576825 -73.965094  
81   40.727847 -73.982226  
100  40.764454 -73.831773  
105  40.614768 -74.031979  
155  40.770826 -73.738898  
163  40.797307 -73.964286  
188  40.572572 -74.116479  
206  40.672321 -73.977050  
230  40.708323 -73.901435  
253  40.710861 -73.958001  
263  40.745652 -73.918193  
291  40.707144 -73.958115

### Let's create a map to see all clusters.

In [81]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(kr_merged['Latitude'], kr_merged['Longitude'], kr_merged['Neighborhood'], kr_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters